Scrapy Class


In [1]:
import scrapy
# Import crawler process
from scrapy.crawler import CrawlerProcess


class laprensa_spider(scrapy.Spider):
    name = 'laprensa_spider'
    global news_list


    def start_requests(self):
        urls = pages
        for url in urls:
            yield scrapy.Request(url=url, callback=self.parse)

    def parse(self, response):
        links = response.xpath('//h4[@class="title "]/a/@href').extract()
        for link in links:
            yield response.follow(url=link, callback=self.parse2)

    def parse2(self, response):
        # Extract the title and text
        title = response.css('h1.title::text').extract_first().strip()
        text = response.xpath('//div[contains(@id,"content-body")]/p//text()').extract()
        # Join the text
        text = ' '.join(text).strip()
        # Construct the new and clean
        article = title + ": " + text
        article = article.strip()
        article = article.replace("\n", " ")
        article = article.rstrip("Síguenos en Facebook:  La Prensa Oficial  y en Twitter:  @laprensaoem")
        article = article.strip()
        # date
        date = response.xpath('//p[@class="published-date"]/text()').extract_first()
        date = date.lstrip("\n\xa0 / ")
        date = date.rstrip("\n")
        new_dictionary = {"url": response.url, "date": date, "article": article}
        news_list.append(new_dictionary)

Scrapy the web

In [2]:
pages = []
for i in range(1000):
    page = 'https://www.la-prensa.com.mx/barebone/wf.template/config.default.master.withoutgroupcount?q=alcald%C3%ADa&section=2403&page=' + str(i + 1) + '&contentType=story&sort=lastmodifieddate&order=DESC'
    pages.append(page)



news_list = []
process = CrawlerProcess()
process.crawl(laprensa_spider)
process.start()

2024-10-07 20:13:44 [scrapy.utils.log] INFO: Scrapy 2.11.2 started (bot: scrapybot)
2024-10-07 20:13:44 [scrapy.utils.log] INFO: Versions: lxml 5.3.0.0, libxml2 2.12.9, cssselect 1.2.0, parsel 1.9.1, w3lib 2.2.1, Twisted 24.7.0, Python 3.10.12 (main, Sep 11 2024, 15:47:36) [GCC 11.4.0], pyOpenSSL 24.2.1 (OpenSSL 3.3.2 3 Sep 2024), cryptography 43.0.1, Platform Linux-5.15.153.1-microsoft-standard-WSL2-x86_64-with-glibc2.35
2024-10-07 20:13:44 [scrapy.addons] INFO: Enabled addons:
[]
2024-10-07 20:13:44 [py.warnings] WARNING: /home/christian/taller/crime-prediction-monitoring-cdmx/.venv/lib/python3.10/site-packages/scrapy/utils/request.py:254: ScrapyDeprecationWarning: '2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a f

In [6]:
print(len(news_list))

print(news_list[12])

10000
{'url': 'https://www.la-prensa.com.mx/policiaca/acribillan-a-policia-en-iztapalapa-detienen-a-sujeto-que-lo-habria-citado-via-telefonica-12566811.html', 'date': 'martes 17 de septiembre de 2024', 'article': 'Acribillan a policía en Iztapalapa; Detienen a sujeto que lo habría citado vía telefónica: Ezequiel “A”, un agente de la Secretaría de Seguridad Ciudadana de la Ciudad de México fue asesinado a tiros en calles de la Alcaldía Iztapalapa. El presunto sospechoso del crimen fue detenido y remitido ante las autoridades ministeriales. Las primeras investigaciones de la policía señalan que el crimen ocurrió la noche del sábado después de que el policía de la Secretaría de Seguridad Ciudadana de la CdMx recibió una llamada telefónica y salió de su domicilio. Los encargados de las investigaciones señalan que el policía de manera repentina recibió una llamada telefónica, para luego de ello salir, pero éste ya no regresó, pues fue ultimado a balazos. La escena del crimen fue acordonada 

Removing teasers

In [4]:
import re 

def clean_teaser(text):
    regex = r"Policiaca\s+[A-Z]+.+?\s{3,}"
    text = re.sub(regex, " ", text)
    text = re.sub(r"\s{2,}", " ", text)
    return text



In [5]:
for text in news_list:
    text['article'] = clean_teaser(text['article'])

print(len(news_list))

print(news_list[15])

10000
{'url': 'https://www.la-prensa.com.mx/policiaca/muere-persona-apunalada-tras-oponerse-a-asalto-en-tacuba-12530439.html', 'date': 'lunes 9 de septiembre de 2024', 'article': 'Muere persona apuñalada tras riña en la zona de Tacuba; hay un detenido: Un muerto con arma punzocortante, fue el saldo de una riña que tuvo lugar la tarde de este lunes sobre la calzada México Tacuba, afuera de un conocido cine para adultos, donde también se registró una balacera. Hay un detenido por estos hechos. Los primeros reportes refieren que la víctima salió de dicho inmueble junto a otros dos hombres, cuando comenzaron a hacerse de palabras, escalaron a los golpes y en el momento más tenso, desenfundaron la pistola y el arma blanca. Algunas detonaciones se escucharon en la calle, así como los gritos de vendedores y transeuntes, pero fue con el arma punzocortante que la muerte sorprendió a un hombre de entre 30 y 35 años de edad, dentro de la colonia Tacuba. La balacera provocó una movilización polici